# High Performance/Throughput Computing

In [1]:
N = 10000000

In [2]:
def f(x):
    y = 0.0
    for i in range(N):
        y += x
    return y

In [3]:
f(0.01)

99999.99998630969

In [4]:
%timeit f(0.01)

1 loops, best of 3: 564 ms per loop


## Cython

[Cython](http://cython.org/) ist ein Compiler,
der Cython Code in C/C++ Code übersetzt und mit der Python C-Bibliothek verbindet.
Dies eignet sich hervorragend dazu,
um langsame Teile eines größeren Python Programmes selektiv zu beschleunigen.
Dies wird dadurch erreicht, dass einzelne Funktionen oder Klassen in die Sprache "*Cython*" umgeschrieben werden.
Dies ist nicht besonders schwierig, da Cython eine Obermenge einer Untermenge der Python Sprache ist:
das heißt, einige komplexere Programmstrukturen gibt es nicht, dafür aber Erweiterungen wie z.B. native Typenbezeichnungen.

Die einzige wirkliche Herausforderung ist,
genau zu verstehen welche Datentypen im Spiel sind und
wie aufwändig die eventuelle Konvertierung der einzelnen Objekte zwischen C/C++ und Python ist.
In der [Dokumentation](http://docs.cython.org/) gibt es dazu viele Beispiele mit anschaulichen Erklärungen.

Im folgenden wird nun Cython durch die `cythonmagic` Extension geladen,
die eingangs vorgestellte Python Funktion nach Cython umgeschrieben,
und in der Zelle mittels des `%%cython` Magic-Commandos ausgeführt.

Von der im Hintergrund ablaufenden Compilierung nach C,
das Linken mit den Python Bibliotheken,
und das anschließende dynamische laden in den aktuellen Python-Kernel bekommt man nichts mit --
es dauert nur ein paar Sekunden, die sich dann später durch die beschleunigte Ausführungszeit wieder leicht einholen lassen ;-)

In [5]:
%load_ext Cython

In [6]:
%%cython
cimport cython
@cython.boundscheck(False)
cpdef f_cy(float x, int N):
    cdef double y = 0.0
    cdef int i
    for 0 <= i <= N:
        y += x
    return y

Kontrolle, dass das Ergebnis stimmt und anschließendes Benchmark mit `%timeit`

In [7]:
f_cy(0.01, N)

100000.0077648256

In [8]:
%timeit f_cy(0.01, N)

100 loops, best of 3: 9.63 ms per loop


Die `--annotate` Option zeigt in gelb genauer an,
was wo Konvertierungen oder Python-Objekte noch im Spiel sind (die das Programm langam machen):

In [9]:
%%cython --annotate
cimport cython
@cython.boundscheck(False)
cpdef f_cy(float x, int N):
    cdef double y = 0.0
    cdef int i
    for 0 <= i <= N:
        y += x
    return y

## Cython & OpenMP

OpenMP ist ein älteres Programmierhilfsmittel, um Schleifen und parallelisierbare Datenstrukturen im Code einfach ausdrücken zu können.
Die Arbeit wird hierfür auf alle CPU-Kerne verteilt.
In dem hier vorgestellten Beispiel ist es die Funktion `prange`, welche diese in Kombination mit der Addition der Ypsilons erledigt.
Implizit wird hier auf die [Nebenläufigkeit](http://de.wikipedia.org/wiki/Nebenl%C3%A4ufigkeit) der Berechnung und dem anschließenden zusammenführen der Ergebnisse aufgepasst!

In [10]:
%%cython --compile-args=-fopenmp --link-args=-fopenmp

cimport cython
from cython.parallel import parallel, prange

@cython.boundscheck(False)
cpdef f_cy_omp(float x, int N):
    cdef double y = 0.0
    cdef Py_ssize_t i
    with nogil:
        for i in prange(N):
            y += x
    return y

In [11]:
f_cy_omp(0.01, N)

99999.99776482582

In [12]:
%timeit f_cy_omp(0.01, N)

100 loops, best of 3: 2.77 ms per loop
